In [1]:
# ****************************************************
# https://realpython.com/primer-on-python-decorators/
# ****************************************************
#

In [8]:
# *********************************************************************************
# Decorators...
#
# A "decorator" is a function that takes another function and extends the behavior 
# of the latter function without explicitly modifying it.
#
# >>>>> decorators wrap a function, modifying its behavior.
# *********************************************************************************

def my_decorator(func):
    def wrapper():
        print("*** Inside wrapper, before func()")
        func()
        print("*** Inside wrapper, AFTER  func()")
    return wrapper

def say_whee():
    print("Whee!")

say_whee()
print("(1): ", say_whee)

print(say_whee())
print()

# NOTE:
#
# This is a variable   This is a function NAME
#  |||||                ||||||||
#  vvvvv                vvvvvvvv
say_whee = my_decorator(say_whee)

say_whee()
print("2: ", say_whee)
print(say_whee())


Whee!
(1):  <function say_whee at 0x7f8d60531dc0>
Whee!
None

*** Inside wrapper, before func()
Whee!
*** Inside wrapper, AFTER  func()
2:  <function my_decorator.<locals>.wrapper at 0x7f8d6057adc0>
*** Inside wrapper, before func()
Whee!
*** Inside wrapper, AFTER  func()
None


In [10]:






# Syntactic Sugar
# The way you decorated say_whee() above is a little clunky. 
# (1) First of all, you end up typing the name say_whee three times. 
# (2) The decoration gets a bit hidden away below the definition of the function

# Python allows you to use decorators in a simpler way with the @ symbol, 
# sometimes called the “pie” syntax. 

def my_decorator(func):
    def wrapper():
        print("*** Inside wrapper, before func()")
        func()
        print("*** Inside wrapper, AFTER  func()")
    return wrapper

# ******************************************************
# This is equivalent to:
#
#     say_whee = my_decorator(say_whee)
# ******************************************************
@my_decorator
def say_whee():
    print("Whee!")

print(say_whee())

*** Inside wrapper, before func()
Whee!
*** Inside wrapper, AFTER  func()
None


In [9]:
# **********************************************
# Decorator that calls a function twice:
# **********************************************

def do_twice(func):
    def wrapper_do_twice():
        func()
        func()
    return wrapper_do_twice

@do_twice
def say_whee():
    print("Whee!")

print(say_whee())




Whee!
Whee!
None


In [10]:
# %%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%
# QUESTION: how to make decorators that take arguments ???
# %%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%
@do_twice
def greet(x):
    print("Hello ", x")

SyntaxError: EOL while scanning string literal (1866654648.py, line 6)

In [3]:
# *******************************************
# Decorator with ARBITRARY arguments
# *******************************************

def do_twice(func):
    def wrapper_do_twice(*args, **kwargs):
        func(*args, **kwargs)
        func(*args, **kwargs)
    return wrapper_do_twice

@do_twice
def greet(x):
    print("Hello ", x)

greet("World")




# %%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%
# Explanation, see: 005-unpack-op.ipynb
# %%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%





Hello  World
Hello  World


In [4]:
# %%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%
# Decorator functions that returns values
# %%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%

@do_twice
def return_greeting(name):
    print("Creating greeting")
    return f"Hi {name}"

hi_adam = return_greeting("Adam")
print(hi_adam)

# "return_greating() was called twice, but....
# because the do_twice_wrapper() does NOT return a value, 
# the call return_greeting("Adam") ended up returning None.

Creating greeting
Creating greeting
None


In [5]:
# To fix this, you need to make sure the wrapper function returns 
# the return value of the decorated function:

def do_twice(func):
    def wrapper_do_twice(*args, **kwargs):
        func(*args, **kwargs)
        return func(*args, **kwargs)
    return wrapper_do_twice

hi_adam = return_greeting("Adam")
print(hi_adam)

# "return_greating() was called twice, but....
# only the return value of the last call was returned...

Creating greeting
Creating greeting
None


In [24]:
# %%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%
# Recipe for defining decorators
# %%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%

import functools

def decorator(func):
    @functools.wraps(func)
    def wrapper_decorator(*args, **kwargs):
        # ---------------------------------------
        # Do something before (insert code here)
        # ---------------------------------------
        value = func(*args, **kwargs)
        # ---------------------------------------
        # Do something after  (insert code here)
        # ---------------------------------------
        return value
    return wrapper_decorator

@decorator
def func(....)
    .....
    return...

# ===========================================================
# We now show some useful decorator functions
# ===========================================================



         DO NOT RUN THIS CELL !!! (You will get syntax error)




SyntaxError: invalid syntax (4072102981.py, line 21)

In [20]:
# ***************************************************************
# Timer decorator:
#
#    measure the time a function takes to execute and 
#    print the duration to the console.
# ***************************************************************

import functools
import time

def timer(func):
    """Print the runtime of the decorated function"""
    @functools.wraps(func)
    def wrapper_timer(*args, **kwargs):
        start_time = time.perf_counter()    # 1
        
        value = func(*args, **kwargs)       # Run the function
        
        end_time = time.perf_counter()      # 2
        
        run_time = end_time - start_time    # 3
        print(f"Finished '{func.__name__}' in {run_time:.4f} secs")
        return value
    return wrapper_timer


In [21]:
# Function:

def waste_some_time(num_times):
    for _ in range(num_times):
        sum([i**2 for i in range(10000)])

waste_some_time(10)

In [22]:
# Time the execution time for he function:

@timer
def waste_some_time(num_times):
    for _ in range(num_times):
        sum([i**2 for i in range(10000)])
        
waste_some_time(10)

Finished 'waste_some_time' in 0.0280 secs


In [27]:
# ***************************************************************
# Debug decorator:
#
#    Prints the arguments and return value of a function call
# ***************************************************************

import functools

def debug(func):
    """Print the function signature and return value"""
    @functools.wraps(func)
    def wrapper_debug(*args, **kwargs):
        args_repr = [repr(a) for a in args]                      # 1
        kwargs_repr = [f"{k}={v!r}" for k, v in kwargs.items()]  # 2
        signature = ", ".join(args_repr + kwargs_repr)           # 3
        print(f"Calling {func.__name__}({signature})")
        
        value = func(*args, **kwargs)
        
        print(f"{func.__name__!r} returned {value!r}")           # 4
        
        return value
    return wrapper_debug

# Explanation:
#
#  (1) Create a list of the positional arguments. 
#      It uses repr() to get a nice string representing each argument.
#  (2) Create a list of the keyword arguments. 
#      The f-string formats each argument as key=value where 
#      the !r specifier means that repr() is used to represent the value.
#  (3) The lists of positional and keyword arguments is joined together 
#      into one signature string with each argument separated by a comma.
#  (4) The return value is printed after the function is executed.


In [29]:
# Try the debug wrapper:

@debug
def make_greeting(name, age=None):
    if age is None:
        return f"Howdy {name}!"
    else:
        return f"Whoa {name}! {age} already, you are growing up!"

make_greeting("John")

Calling make_greeting('John')
'make_greeting' returned 'Howdy John!'


'Howdy John!'

In [31]:
# It works recursively too:

import math

# Apply a decorator to a standard library function
# We can't use @debug because we don't define it
# So use the "traditional" way:

math.factorial = debug(math.factorial)

# e ~= 1/1! + 1/2! + 1/3! + ....
def approximate_e(terms=5):
    return sum(1 / math.factorial(n) for n in range(terms))

approximate_e()

Calling factorial(0)
'factorial' returned 1
Calling factorial(1)
'factorial' returned 1
Calling factorial(2)
'factorial' returned 2
Calling factorial(3)
'factorial' returned 6
Calling factorial(4)
'factorial' returned 24


2.708333333333333

In [ ]:
# *******************************************************
# Postlude:
#
#   There are a LOT more examples on the page:
#
#       https://realpython.com/primer-on-python-decorators/
#
# Like Decorator on classes... nested decorators....
#
# I think I want to learn ML and move on...
#
#   ** I may revisit the page in the future ****
# *********************************************************
